When you download from Google Drive, folder structure and files comes in a bunch of different Zip folders. This is to reform the folder/file structure in NextCloud

In [ ]:
# this script creates the folder structure. note that it does modify folder names and records original vs. changed folder names

import os
import zipfile
import tkinter as tk
from tkinter import filedialog, messagebox, ttk

MAX_FOLDER_NAME_LENGTH = 50  # Maximum length for each folder name segment
MAX_PATH_LENGTH = 260        # Maximum length for the entire path

def select_zip_files():
    """Open file dialog to select multiple ZIP files."""
    zip_files = filedialog.askopenfilenames(
        title="Select ZIP files",
        filetypes=[("ZIP files", "*.zip")]
    )
    return zip_files

def select_output_directory():
    """Open directory dialog to select output folder."""
    output_directory = filedialog.askdirectory(title="Select Output Directory")
    return output_directory

def sanitize_and_truncate_folder_name(folder_name):
    """Sanitize folder name by removing trailing whitespace and truncating if needed."""
    folder_name = folder_name.strip()  # Remove trailing spaces
    if len(folder_name) > MAX_FOLDER_NAME_LENGTH:
        truncated_name = folder_name[:MAX_FOLDER_NAME_LENGTH]
        return truncated_name, folder_name  # Return truncated and original names
    return folder_name, None  # No truncation needed

def create_folder_structure_with_progress(zip_files, output_directory, progress_bar, progress_label):
    """Reconstruct folder structure from ZIP files with truncation for long paths and progress tracking."""
    error_log = []  # Log to capture folder creation issues
    truncation_log = []  # To record original folder names for truncated folders

    total_entries = sum(len(zipfile.ZipFile(zip_file).namelist()) for zip_file in zip_files)
    processed_entries = 0

    for zip_file in zip_files:
        with zipfile.ZipFile(zip_file, 'r') as zip_ref:
            for member in zip_ref.namelist():
                # Get the directory path
                original_directory_path = os.path.join(output_directory, os.path.dirname(member))
                truncated_directory_path = output_directory

                # Process each folder level in the path
                for part in os.path.normpath(original_directory_path).split(os.sep):
                    sanitized_name, original_name = sanitize_and_truncate_folder_name(part)
                    truncated_directory_path = os.path.join(truncated_directory_path, sanitized_name)

                    # Record truncation if it occurred
                    if original_name:
                        truncation_log.append(f"Truncated '{original_name}' to '{sanitized_name}' in path: {truncated_directory_path}")

                # Ensure path length does not exceed Windows limit
                if len(truncated_directory_path) > MAX_PATH_LENGTH:
                    error_log.append(f"Path too long: {truncated_directory_path}")
                    continue

                # Create the directory if it doesn't exist
                try:
                    if not os.path.exists(truncated_directory_path):
                        os.makedirs(truncated_directory_path, exist_ok=True)
                except FileNotFoundError as e:
                    # Log specific error for debugging
                    error_log.append(f"Error creating {truncated_directory_path}: {e}")
                    continue

                # Update progress
                processed_entries += 1
                progress = processed_entries / total_entries * 100
                progress_bar["value"] = progress
                progress_label.config(text=f"Processing folder {processed_entries} of {total_entries}")
                progress_bar.update_idletasks()

    # Write truncation log to a file
    if truncation_log:
        with open(os.path.join(output_directory, "original_folder_names.txt"), "w") as log_file:
            log_file.write("\n".join(truncation_log))

    # Log any errors
    if error_log:
        with open("folder_creation_error_log.txt", "w") as log_file:
            log_file.write("\n".join(error_log))
        messagebox.showwarning("Folder Creation Completed with Errors", 
                               "Folder structure was created, but some errors occurred. Check 'folder_creation_error_log.txt' for details.")
    else:
        messagebox.showinfo("Success", "Folder structure created successfully!")

def main():
    # Set up tkinter window
    root = tk.Tk()
    root.title("Rebuild Folder Structure from ZIP Files")
    root.geometry("400x300")

    # Instruction label
    label = tk.Label(root, text="Select ZIP files and an output directory to recreate folder structure")
    label.pack(pady=10)

    # Progress bar and label
    progress_label = tk.Label(root, text="Progress: 0%")
    progress_label.pack(pady=5)
    progress_bar = ttk.Progressbar(root, orient="horizontal", length=300, mode="determinate")
    progress_bar.pack(pady=5)

    # Start button
    def start_structure_creation():
        zip_files = select_zip_files()
        output_directory = select_output_directory()

        if not zip_files or not output_directory:
            messagebox.showerror("Error", "Please select both ZIP files and an output directory.")
            return

        # Create folder structure only with progress and truncation handling
        create_folder_structure_with_progress(zip_files, output_directory, progress_bar, progress_label)

    # Start button
    start_button = tk.Button(root, text="Start Folder Structure Creation", command=start_structure_creation)
    start_button.pack(pady=20)

    # Run tkinter main loop
    root.mainloop()

if __name__ == "__main__":
    main()


In [14]:
import os
import zipfile
import shutil
import tkinter as tk
from tkinter import filedialog, messagebox, ttk


def select_zip_files():
    """Open file dialog to select multiple ZIP files."""
    zip_files = filedialog.askopenfilenames(
        title="Select ZIP files",
        filetypes=[("ZIP files", "*.zip")]
    )
    return zip_files


def select_output_directory():
    """Open directory dialog to select output folder where the structure already exists."""
    output_directory = filedialog.askdirectory(title="Select Output Directory")
    return output_directory


def select_original_names_file():
    """Open file dialog to select the 'original_folder_names.txt'."""
    file_path = filedialog.askopenfilename(
        title="Select original_folder_names.txt",
        filetypes=[("Text files", "*.txt")]
    )
    return file_path


def get_original_folder_names(original_file_names_file):
    """Read the original folder names from the file."""
    with open(original_file_names_file, "r") as f:
        return f.readlines()


def extract_files(zip_files, output_directory, progress_bar, progress_label):
    """Extract files from multiple ZIP files into the target directory based on existing folder structure."""
    error_log = []  # Log to capture errors during extraction
    total_entries = sum(len(zipfile.ZipFile(zip_file).namelist()) for zip_file in zip_files)
    processed_entries = 0

    for zip_file in zip_files:
        with zipfile.ZipFile(zip_file, 'r') as zip_ref:
            for member in zip_ref.namelist():
                # Construct the target path based on the member's folder structure in the ZIP
                target_path = os.path.join(output_directory, member)

                # Check if the corresponding folder exists in the output directory
                if not os.path.exists(os.path.dirname(target_path)):
                    error_log.append(f"Directory missing, skipping: {target_path}")
                    continue

                # Extract the file to the correct path in the output directory
                try:
                    with zip_ref.open(member) as source, open(target_path, "wb") as target_file:
                        shutil.copyfileobj(source, target_file)
                except Exception as e:
                    error_log.append(f"Error extracting {member}: {e}")
                    continue

                # Update progress
                processed_entries += 1
                progress = processed_entries / total_entries * 100
                progress_bar["value"] = progress
                progress_label.config(text=f"Extracting file {processed_entries} of {total_entries}")
                progress_bar.update_idletasks()

    # Log any errors
    if error_log:
        with open("file_extraction_error_log.txt", "w") as log_file:
            log_file.write("\n".join(error_log))
        messagebox.showwarning("Extraction Completed with Errors", 
                               "File extraction was completed, but some errors occurred. Check 'file_extraction_error_log.txt' for details.")
    else:
        messagebox.showinfo("Success", "Files extracted successfully!")


def main():
    # Set up tkinter window
    root = tk.Tk()
    root.title("Extract Files from ZIP into Existing Folder Structure")
    root.geometry("400x300")

    # Instruction label
    label = tk.Label(root, text="Select ZIP files and an output directory to extract files")
    label.pack(pady=10)

    # Progress bar and label
    progress_label = tk.Label(root, text="Progress: 0%")
    progress_label.pack(pady=5)
    progress_bar = ttk.Progressbar(root, orient="horizontal", length=300, mode="determinate")
    progress_bar.pack(pady=5)

    # Start button
    def start_file_extraction():
        zip_files = select_zip_files()

        if not zip_files:
            messagebox.showerror("Error", "Please select at least one ZIP file.")
            return

        # Select the output directory where the folder structure already exists
        output_directory = select_output_directory()

        if not output_directory:
            messagebox.showerror("Error", "Please select the output directory.")
            return

        # Select the 'original_folder_names.txt' file to ensure folder truncations were logged
        original_file_names_file = select_original_names_file()

        if not original_file_names_file:
            messagebox.showerror("Error", "Please select the 'original_folder_names.txt' file.")
            return

        # Get the list of original folder names from the file
        folder_names = get_original_folder_names(original_file_names_file)

        # Proceed with file extraction
        extract_files(zip_files, output_directory, progress_bar, progress_label)

    # Start button
    start_button = tk.Button(root, text="Start File Extraction", command=start_file_extraction)
    start_button.pack(pady=20)

    # Run tkinter main loop
    root.mainloop()


if __name__ == "__main__":
    main()


: 

In [11]:
import os
import zipfile
import tkinter as tk
from tkinter import filedialog


MAX_FOLDER_NAME_LENGTH = 50  # Maximum length for each folder name segment


def select_zip_files():
    """Open file dialog to select multiple ZIP files."""
    zip_files = filedialog.askopenfilenames(
        title="Select ZIP files",
        filetypes=[("ZIP files", "*.zip")]
    )
    return zip_files


def select_output_directory():
    """Open directory dialog to select output folder where the structure already exists."""
    output_directory = filedialog.askdirectory(title="Select Output Directory")
    return output_directory


def select_original_names_file():
    """Open file dialog to select the 'original_folder_names.txt'."""
    file_path = filedialog.askopenfilename(
        title="Select original_folder_names.txt",
        filetypes=[("Text files", "*.txt")]
    )
    return file_path


def get_original_folder_names(original_file_names_file):
    """Read the original folder names from the file."""
    with open(original_file_names_file, "r") as f:
        return f.readlines()


def sanitize_and_truncate_folder_name(folder_name):
    """Sanitize folder name by removing trailing whitespace and truncating if needed."""
    folder_name = folder_name.strip()  # Remove trailing spaces
    if len(folder_name) > MAX_FOLDER_NAME_LENGTH:
        truncated_name = folder_name[:MAX_FOLDER_NAME_LENGTH]
        return truncated_name, folder_name  # Return truncated and original names
    return folder_name, None  # No truncation needed


def analyze_folder_structure(zip_files, output_directory):
    """Analyze folder structure in ZIP files and map to the existing folder structure in the output directory."""
    zip_folder_structure = {}
    output_folder_structure = {}

    # Analyze folder structure from the ZIP files (full paths)
    print("Analyzing ZIP files...\n")
    for zip_file in zip_files:
        with zipfile.ZipFile(zip_file, 'r') as zip_ref:
            for member in zip_ref.namelist():
                full_zip_path = os.path.join(zip_file, member)  # Full path within the ZIP
                folder = os.path.dirname(member)  # Folder path within the ZIP file
                zip_folder_structure[folder] = full_zip_path  # Store full path from ZIP
                print(f"ZIP Folder Path: {folder}, Full Path: {full_zip_path}")

    print("\nAnalyzing output directory...\n")
    # Analyze folder structure in the output directory (full paths)
    for root, dirs, files in os.walk(output_directory):
        for dir_name in dirs:
            output_full_path = os.path.join(root, dir_name)  # Full path in output directory
            relative_path = os.path.relpath(output_full_path, output_directory)  # Relative path from output dir
            output_folder_structure[relative_path] = output_full_path
            print(f"Output Folder Path: {relative_path}, Full Path: {output_full_path}")

    # Map folder structure from ZIP to output folder structure
    folder_mapping = {}
    print("\nComparing ZIP Folder Paths with Output Folder Paths...\n")
    for zip_folder in zip_folder_structure:
        truncated_folder, original_folder = sanitize_and_truncate_folder_name(zip_folder)
        output_path = output_folder_structure.get(truncated_folder)  # Get the full output folder path

        print(f"Comparing ZIP Folder: {zip_folder} (Truncated: {truncated_folder}) with Output Folders...")
        if output_path:
            folder_mapping[zip_folder] = output_path
            print(f"Mapping found: {zip_folder} -> {output_path}")
        else:
            folder_mapping[zip_folder] = None  # Folder not found in output directory
            print(f"No matching folder in Output Directory for: {zip_folder}")
    
    return folder_mapping


def output_folder_mapping(folder_mapping):
    """Output the folder structure mapping to a text file."""
    with open("folder_structure_mapping.txt", "w") as file:
        for zip_folder, output_folder in folder_mapping.items():
            if output_folder:
                file.write(f"ZIP Folder: {zip_folder}\nMapped to Output Folder: {output_folder}\n\n")
            else:
                file.write(f"ZIP Folder: {zip_folder}\nNo matching folder in Output Directory\n\n")

    print("\nFolder structure mapping has been saved to 'folder_structure_mapping.txt'.\n")


def main():
    # Set up tkinter window
    root = tk.Tk()
    root.title("Generate Folder Structure Mapping")
    root.geometry("400x300")

    # Instruction label
    label = tk.Label(root, text="Select ZIP files and an output directory to generate folder structure mapping")
    label.pack(pady=10)

    # Start button
    def start_folder_mapping():
        zip_files = select_zip_files()

        if not zip_files:
            messagebox.showerror("Error", "Please select at least one ZIP file.")
            return

        # Select the output directory where the folder structure already exists
        output_directory = select_output_directory()

        if not output_directory:
            messagebox.showerror("Error", "Please select the output directory.")
            return

        # Select the 'original_folder_names.txt' file to ensure folder truncations were logged
        original_file_names_file = select_original_names_file()

        if not original_file_names_file:
            messagebox.showerror("Error", "Please select the 'original_folder_names.txt' file.")
            return

        # Get the list of original folder names from the file
        folder_names = get_original_folder_names(original_file_names_file)

        # Map folder structure from ZIP files to the output directory
        folder_mapping = analyze_folder_structure(zip_files, output_directory)

        # Output the folder structure mapping to a text file
        output_folder_mapping(folder_mapping)

        messagebox.showinfo("Success", "Folder structure mapping has been generated and saved.")

    # Start button
    start_button = tk.Button(root, text="Generate Folder Mapping", command=start_folder_mapping)
    start_button.pack(pady=20)

    # Run tkinter main loop
    root.mainloop()


if __name__ == "__main__":
    main()


Analyzing ZIP files...

ZIP Folder Path: UMN Files/Hippen Lab Back-up/Tissue Photos, Full Path: C:/Users/lehnen/Downloads/UMN Files-20241105T080720Z-003.zip\UMN Files/Hippen Lab Back-up/Tissue Photos/394 gut 4x (2)(XGVHD31).tif
ZIP Folder Path: UMN Files/Hippen Lab Back-up/Tissue Photos, Full Path: C:/Users/lehnen/Downloads/UMN Files-20241105T080720Z-003.zip\UMN Files/Hippen Lab Back-up/Tissue Photos/392 gut 10x (2)(XGVHD31).tif
ZIP Folder Path: UMN Files/Hippen Lab Back-up/Tissue Photos, Full Path: C:/Users/lehnen/Downloads/UMN Files-20241105T080720Z-003.zip\UMN Files/Hippen Lab Back-up/Tissue Photos/391 gut 4x (2)(XGVHD31).tif
ZIP Folder Path: UMN Files/Hippen Lab Back-up/Tissue Photos, Full Path: C:/Users/lehnen/Downloads/UMN Files-20241105T080720Z-003.zip\UMN Files/Hippen Lab Back-up/Tissue Photos/393 gut 4x (3)(XGVHD31).tif
ZIP Folder Path: UMN Files/Hippen Lab Back-up/Tissue Photos, Full Path: C:/Users/lehnen/Downloads/UMN Files-20241105T080720Z-003.zip\UMN Files/Hippen Lab Back-

In [ ]:
# this just helped me see which folder to select for output folder so that the script could map in the input to the output correctly

import os
import zipfile
import tkinter as tk
from tkinter import filedialog


def select_zip_files():
    """Open file dialog to select multiple ZIP files."""
    zip_files = filedialog.askopenfilenames(
        title="Select ZIP files",
        filetypes=[("ZIP files", "*.zip")]
    )
    return zip_files


def select_output_directory():
    """Open directory dialog to select output folder where the structure already exists."""
    output_directory = filedialog.askdirectory(title="Select Output Directory")
    return output_directory


def list_folders_in_zip(zip_files):
    """List all folders from the input ZIP files."""
    zip_folders = set()  # Using a set to avoid duplicates
    for zip_file in zip_files:
        with zipfile.ZipFile(zip_file, 'r') as zip_ref:
            for member in zip_ref.namelist():
                folder = os.path.dirname(member)  # Get the folder path from the ZIP
                zip_folders.add(folder)
    return zip_folders


def list_folders_in_output_directory(output_directory):
    """List all folders in the output directory."""
    output_folders = set()  # Using a set to avoid duplicates
    for root, dirs, _ in os.walk(output_directory):
        for dir_name in dirs:
            full_path = os.path.relpath(os.path.join(root, dir_name), output_directory)
            output_folders.add(full_path)
    return output_folders


def write_to_txt(file_name, folders):
    """Write list of folders to a text file."""
    with open(file_name, "w") as file:
        for folder in sorted(folders):
            file.write(f"{folder}\n")


def main():
    # Set up tkinter window
    root = tk.Tk()
    root.title("List Folder Structures from ZIP and Output Directory")
    root.geometry("400x300")

    # Instruction label
    label = tk.Label(root, text="Select ZIP files and output directory to list folder structures")
    label.pack(pady=10)

    # Start button
    def start_folder_listing():
        zip_files = select_zip_files()

        if not zip_files:
            messagebox.showerror("Error", "Please select at least one ZIP file.")
            return

        # Select the output directory where the folder structure already exists
        output_directory = select_output_directory()

        if not output_directory:
            messagebox.showerror("Error", "Please select the output directory.")
            return

        # List folders from ZIP files
        zip_folders = list_folders_in_zip(zip_files)

        # List folders from output directory
        output_folders = list_folders_in_output_directory(output_directory)

        # Write both folder lists to text files
        write_to_txt("zip_folders.txt", zip_folders)
        write_to_txt("output_folders.txt", output_folders)

        messagebox.showinfo("Success", "Folder structures have been saved to 'zip_folders.txt' and 'output_folders.txt'.")

    # Start button
    start_button = tk.Button(root, text="List Folder Structures", command=start_folder_listing)
    start_button.pack(pady=20)

    # Run tkinter main loop
    root.mainloop()


if __name__ == "__main__":
    main()
